In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

# Imports
import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)


In [2]:
def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2 and Pooling Layer #2
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Dense Layer
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits Layer
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }

  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [4]:
mnist = tf.contrib.learn.datasets.load_dataset("mnist")
train_data = mnist.train.images # Returns np.array
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
eval_data = mnist.test.images # Returns np.array
eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz


In [16]:
# Create the Estimator
mnist_classifier = tf.estimator.Estimator(
    model_fn=cnn_model_fn, model_dir="./tmp/mnist_convnet_model")

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {}


In [14]:
# Set up logging for predictions
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

In [15]:
# Train the model
train_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": train_data},
    y=train_labels,
    batch_size=100,
    num_epochs=None,
    shuffle=True)

mnist_classifier.train(
    input_fn=train_input_fn,
    steps=20000,
    hooks=[logging_hook])

INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:loss = 2.32699, step = 1
INFO:tensorflow:probabilities = [[ 0.10442551  0.11103747  0.07784987  0.10662968  0.10436178  0.08684132
   0.09096897  0.10759876  0.09934964  0.11093704]
 [ 0.0848325   0.11110836  0.08091376  0.11499827  0.11615341  0.09092258
   0.1011209   0.08210263  0.10614349  0.11170413]
 [ 0.09537248  0.11198346  0.09678178  0.10275554  0.09711336  0.0903471
   0.09605316  0.09038628  0.10741439  0.11179237]
 [ 0.08769733  0.11163731  0.09379885  0.10574214  0.10291747  0.10195597
   0.11238012  0.08921374  0.09950151  0.09515557]
 [ 0.07973753  0.11966613  0.09298074  0.0906641   0.1020156   0.09820994
   0.107574    0.10024477  0.09989587  0.10901134]
 [ 0.08786941  0.13256849  0.07632838  0.09424557  0.10587773  0.09880663
   0.09742386  0.10101457  0.10624765  0.0996177 ]
 [ 0.09467988  0.10489997  0.09175798  0.10151242  

INFO:tensorflow:probabilities = [[ 0.09262809  0.11330751  0.08799167  0.10538737  0.09657172  0.08945248
   0.09107545  0.10273187  0.09576327  0.12509057]
 [ 0.08881018  0.10535768  0.08510149  0.1032306   0.10326415  0.10117266
   0.10065747  0.09204321  0.1052157   0.11514683]
 [ 0.09135544  0.11566785  0.08945613  0.10421858  0.1005877   0.09120329
   0.10095415  0.08920837  0.09774912  0.11959936]
 [ 0.09391602  0.11272518  0.08356686  0.11330054  0.1005105   0.08397367
   0.11068845  0.09656302  0.09420927  0.11054646]
 [ 0.10000557  0.09993324  0.0951578   0.10311442  0.1067795   0.09252539
   0.10621247  0.09287713  0.09698553  0.10640891]
 [ 0.09346743  0.11314734  0.08874758  0.0913526   0.10829598  0.08585172
   0.10004767  0.10974152  0.10095218  0.10839596]
 [ 0.09879441  0.10739249  0.09480423  0.10287904  0.09377131  0.09330472
   0.11095478  0.10037374  0.09131829  0.10640695]
 [ 0.09477245  0.10180818  0.07986983  0.10984456  0.10164721  0.09623293
   0.11082829  0.09

INFO:tensorflow:global_step/sec: 2.03186
INFO:tensorflow:loss = 2.3017, step = 101 (49.217 sec)
INFO:tensorflow:probabilities = [[ 0.10058751  0.10581519  0.0969599   0.1109824   0.08779164  0.09850545
   0.10786883  0.09021682  0.09012078  0.11115146]
 [ 0.10350215  0.10517427  0.08703782  0.10593164  0.10277639  0.08297645
   0.10225432  0.11317971  0.08610538  0.11106192]
 [ 0.10045292  0.08987821  0.09556993  0.11141696  0.09209111  0.09068561
   0.10558714  0.0964206   0.0988989   0.11899856]
 [ 0.09324806  0.12799801  0.09548927  0.11225936  0.09659279  0.08496261
   0.09935694  0.08482081  0.0999833   0.10528879]
 [ 0.11230837  0.12523587  0.07780952  0.11256701  0.09640077  0.09818442
   0.09461195  0.10206917  0.07406546  0.10674743]
 [ 0.09224597  0.11508457  0.09089647  0.11856528  0.10285656  0.08803629
   0.10515866  0.09028283  0.08882183  0.10805155]
 [ 0.08387767  0.10731976  0.08298493  0.10413311  0.09928704  0.10438989
   0.10011089  0.0974106   0.10266478  0.1178213

INFO:tensorflow:probabilities = [[ 0.09172719  0.09846924  0.10393425  0.10464692  0.09696786  0.09320661
   0.11211861  0.08002102  0.10477783  0.11413044]
 [ 0.08139898  0.10550471  0.08548404  0.11767133  0.10378498  0.0943616
   0.1114177   0.09906948  0.09498853  0.10631869]
 [ 0.0938964   0.10998634  0.1058988   0.09354282  0.10723892  0.09781148
   0.09622814  0.08346564  0.1048361   0.10709545]
 [ 0.09185589  0.10548715  0.08574049  0.12026756  0.0971128   0.08476622
   0.09503771  0.09354539  0.09836613  0.12782061]
 [ 0.09848762  0.09901752  0.09051151  0.10978539  0.09607858  0.08319358
   0.12245454  0.09355237  0.10132028  0.10559867]
 [ 0.08901019  0.10155426  0.08823476  0.11804079  0.09169379  0.08488893
   0.09093603  0.10701092  0.1130532   0.11557715]
 [ 0.09206828  0.10625232  0.0976975   0.10493568  0.09415416  0.09529042
   0.10837246  0.10162685  0.1060435   0.09355886]
 [ 0.09754309  0.10031793  0.09236548  0.11941013  0.09906546  0.08764895
   0.08572084  0.103

INFO:tensorflow:global_step/sec: 1.96857
INFO:tensorflow:loss = 2.26172, step = 201 (50.798 sec)
INFO:tensorflow:probabilities = [[ 0.09564427  0.10764915  0.0929362   0.11054455  0.10430208  0.08775935
   0.09029818  0.10167188  0.09668446  0.11250979]
 [ 0.09597372  0.11211842  0.09461978  0.10087854  0.09492949  0.09423329
   0.10359987  0.10329049  0.09970923  0.10064717]
 [ 0.09905267  0.11495154  0.09072599  0.11277127  0.09815084  0.09761631
   0.10483061  0.08512222  0.08958694  0.10719171]
 [ 0.0934768   0.10367512  0.09222817  0.10096066  0.09765507  0.0989939
   0.10391564  0.10825321  0.10440902  0.09643243]
 [ 0.09991227  0.10671452  0.08422194  0.1221724   0.09495953  0.10335118
   0.10184791  0.08657326  0.09596682  0.10428018]
 [ 0.09124085  0.10468392  0.0910932   0.1132061   0.09882303  0.07323185
   0.1064187   0.09955038  0.09780364  0.12394834]
 [ 0.09958035  0.10561243  0.09236184  0.11408117  0.08686761  0.09637111
   0.09982876  0.09752247  0.09690294  0.1108712

...

INFO:tensorflow:global_step/sec: 1.29623
INFO:tensorflow:loss = 0.127311, step = 19801 (77.142 sec)
INFO:tensorflow:probabilities = [[ 0.00003409  0.00003017  0.00000099  0.0001015   0.0000221   0.99930966
   0.00004168  0.00021246  0.00023141  0.00001592]
 [ 0.00000417  0.00035001  0.00004258  0.07505856  0.00009762  0.84278733
   0.00011224  0.00000037  0.0815306   0.00001656]
 [ 0.00098789  0.00011554  0.07574068  0.03056166  0.00010282  0.00737807
   0.00000295  0.00611239  0.61270362  0.26629433]
 [ 0.0000569   0.00005943  0.00000791  0.00067657  0.00487333  0.00048696
   0.00000328  0.03811909  0.00452387  0.95119268]
 [ 0.00010015  0.00000039  0.00000361  0.00000011  0.00020291  0.00003487
   0.9996345   0.00000007  0.00002169  0.00000182]
 [ 0.00000007  0.00001867  0.00000583  0.00067642  0.01010718  0.00062955
   0.00000009  0.00025768  0.0001067   0.98819774]
 [ 0.00002582  0.00000392  0.00001832  0.99930799  0.00000032  0.00032191
   0.00000008  0.00000286  0.00020583  0.000

INFO:tensorflow:probabilities = [[ 0.00000575  0.00001566  0.00026034  0.00002452  0.00000536  0.0000236
   0.00010681  0.00000254  0.99951279  0.00004262]
 [ 0.00142684  0.00704151  0.00060902  0.00226746  0.00310378  0.16021119
   0.00848914  0.00014871  0.81515795  0.0015444 ]
 [ 0.00000002  0.00000007  0.00000321  0.00027837  0.00000021  0.0000002
   0.          0.9996711   0.00000098  0.00004585]
 [ 0.00000245  0.00001441  0.00028258  0.00089569  0.00000033  0.00000747
   0.00000001  0.99580622  0.0000494   0.00294142]
 [ 0.0000026   0.99902797  0.00057489  0.0001938   0.00003951  0.00000242
   0.00008158  0.00004067  0.00003305  0.00000357]
 [ 0.00002402  0.99506086  0.0002732   0.00053234  0.00019637  0.00008475
   0.00002166  0.00269094  0.00075097  0.00036489]
 [ 0.00000004  0.00000045  0.00000602  0.00001057  0.99953556  0.00000419
   0.00000124  0.00022365  0.00000503  0.00021329]
 [ 0.0000015   0.00000019  0.99985933  0.00006965  0.00003547  0.00000034
   0.00002369  0.0000

INFO:tensorflow:global_step/sec: 1.23507
INFO:tensorflow:loss = 0.210092, step = 19901 (80.972 sec)
INFO:tensorflow:probabilities = [[ 0.00002262  0.00092596  0.00876454  0.01139163  0.0000186   0.00000132
   0.00000001  0.9674471   0.00459286  0.00683543]
 [ 0.00000583  0.00018827  0.00046796  0.00241177  0.00005867  0.00040726
   0.00000629  0.00005333  0.99615073  0.00024992]
 [ 0.00941063  0.21572778  0.76274937  0.00073536  0.00063782  0.00092278
   0.0006548   0.0000264   0.00911539  0.00001978]
 [ 0.00000049  0.00000893  0.00007626  0.9972012   0.0000014   0.00022073
   0.00000037  0.00000291  0.00228243  0.0002053 ]
 [ 0.00001786  0.00000026  0.00000061  0.00017071  0.0019593   0.00002463
   0.00000003  0.03789768  0.00000907  0.95991987]
 [ 0.82377523  0.00000788  0.03257587  0.00425887  0.00319804  0.00034037
   0.00406903  0.00001174  0.13106446  0.00069843]
 [ 0.00000037  0.00000011  0.00000001  0.00004622  0.00000087  0.99993491
   0.00000494  0.          0.00000904  0.000

INFO:tensorflow:probabilities = [[ 0.00000707  0.9950859   0.00002724  0.00153097  0.00020819  0.00003652
   0.00005273  0.00078592  0.00208022  0.00018521]
 [ 0.00000196  0.99893624  0.00003828  0.00047565  0.00007019  0.0000022
   0.00000325  0.00007523  0.00019204  0.00020492]
 [ 0.00043631  0.98652923  0.00068982  0.00108989  0.00025258  0.00029427
   0.00118357  0.00094557  0.0081823   0.00039657]
 [ 0.00067204  0.00507335  0.00386854  0.05119799  0.00009173  0.00347793
   0.00013842  0.00038344  0.93461448  0.00048213]
 [ 0.00002265  0.99213785  0.00088288  0.0005814   0.00001747  0.00002932
   0.00000259  0.00541407  0.00080232  0.00010941]
 [ 0.10521042  0.00283113  0.2240261   0.00291738  0.4188579   0.00290515
   0.16651486  0.00085848  0.00975875  0.06611988]
 [ 0.00000248  0.00002631  0.0000656   0.99560827  0.0000022   0.00415195
   0.00000032  0.00000354  0.00009175  0.00004753]
 [ 0.00000068  0.00008342  0.00000207  0.00010623  0.86588115  0.00002147
   0.00000226  0.000

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.0868845.


In [ ]:
# Evaluate the model and print results
eval_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": eval_data},
    y=eval_labels,
    num_epochs=1,
    shuffle=False)
eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
print(eval_results)